# Meteogram
## Here we draw a surface meteogram, from data that we retrieve from our METAR archive.

#### Imports

In [ ]:
import numpy as np
import pandas as pd

import matplotlib.pyplot as plt
from matplotlib.dates import DateFormatter, AutoDateLocator,YearLocator, HourLocator,DayLocator,MonthLocator

from metpy.units import units
from datetime import datetime, timedelta
import seaborn as sns

Set the desired start and end time (UTC), and create strings for the figure title.

In [ ]:
startTime = datetime(2025,3,28,0)
endTime = datetime(2025,3,31,0)
sTimeStr = startTime.strftime(format="%x %H UTC")
eTimeStr = endTime.strftime(format="%x %H UTC")

Create an empty `Dateframe` to which we will concatenate the hourly CSV files in the desired time range.

In [ ]:
df = pd.DataFrame()

Loop over each hour. Concatenate each hour's METARs into the full `Dataframe`.

In [ ]:
curTime = startTime
while (curTime <= endTime):
    print (curTime)
    timeStr = curTime.strftime("%y%m%d%H")
    metarCSV = f'/ktyle_rit/scripts/sflist2/complete/{timeStr}.csv'
    dfTemp = pd.read_csv(metarCSV, sep='\\s+')
    df = pd.concat([df, dfTemp], ignore_index=True)
    curTime = curTime + timedelta(hours=1)

Examine the `Dataframe`

In [ ]:
df

Select the station from which to subset the `Dataframe`.

In [ ]:
site = 'LGA'

Create a new `Dataframe` that contains only the rows for the desired site.

In [ ]:
dfSub = df.query('STN == @site')

Create a new column that represents the date and time as a `datetime64` object.

In [ ]:
# Next line suppresses a warning message. See https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy. 
# This won't be necessary with Pandas version 3 and beyond.

pd.options.mode.copy_on_write = True 

dattim = pd.to_datetime(dfSub['YYMMDD/HHMM'],format="%y%m%d/%H%M", utc=True)
dfSub['DATETIME'] = dattim

Examine the subsetted `Dataframe`.

In [ ]:
dfSub

Select a couple of variables we wish to plot on the meteogram. In this case, 2m temperature and dewpoint.

In [ ]:
var1 = dfSub['TMPC']
var2 = dfSub['DWPC']

Examine one of the variables ... of course, it's a Pandas `Series`.

In [ ]:
var1

Pandas `Series` objects don't support units. We can, however, create **Numpy** arrays from the `Series` *values* attribute and then attach units to them.

In [ ]:
tmpc = var1.values * units('degC')
dwpc = var2.values * units('degC')

Examine one of the units-aware arrays.

In [ ]:
tmpc

Now convert into degrees F.

In [ ]:
tmpf = tmpc.to('degF')
dwpf = dwpc.to('degF')

#### Create the meteogram and save the figure to disk.

In [ ]:
sns.set()

fig, ax = plt.subplots(figsize=(15, 10))

# Improve on the default ticking

ax.xaxis.set_major_locator(HourLocator(interval=3))
hoursFmt = DateFormatter('%d/%H')
ax.xaxis.set_major_formatter(hoursFmt)

ax.plot(dfSub['DATETIME'], tmpf, color='tab:red', label='Temp')
ax.plot(dfSub['DATETIME'], dwpf, color='tab:green', label='Dwpt')

ax.set_title(f'Site: {site}      Date Range: {sTimeStr} - {eTimeStr}')

ax.set_xlabel('Hour (UTC)')
ax.set_ylabel('Temperature °F')
ax.set_xlim(startTime, endTime)
ax.legend(loc='best')

fig.savefig (f'{site}_mgram.png')

<div class="admonition alert alert-success">
    <p class="admonition-title" style="font-weight:bold">Things to try:</p>
    <ol><li><b>Basic</b> Select a site and time range relevant for your case</li>
        <li><b>Basic</b> Create a multi-panel figure, each displaying a variable of interest</li>
        <li><b>Advanced</b> Plot two variables that have different units; create corresponding y-axis labels on the left and right sides of the plot</li></ol>
</div>